# NSMC 데이터에 대해 KT-AI/midm-bitext-S-7B-inst-v1 미세튜닝 과제

## KT-AI/midm-bitext-S-7B-inst-v1 를 NSMC 데이터에 미세 튜닝

- dataset_infos.json


##목표
- 영화 리뷰 텍스트를 프롬프트에 포함하여 모델에 입력하면
- '긍정' 또는 '부정' 이라고 예측 텍스트를 직접 생성

##요건
- NSMC의 train 스플릿 앞쪽 2,000개 이상의 샘플을 학습에 사용
- 테스트는 test 스플릿 앞쪽 1,000개의 샘플만 측정할 것




In [1]:
pip install transformers peft accelerate optimum bitsandbytes trl wandb einops

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.3/168.3 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 9.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 400.9/400.9 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.6/92.6 MB 10.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 133.9/133.9 kB 18.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 69.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 21.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.9/100.9 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.6/190.6 kB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 252.8/252.8 kB 25.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━

In [2]:
import os
from dataclasses import dataclass, field
from typing import Optional
import re

import torch
import tyro
from accelerate import Accelerator
from datasets import load_dataset, Dataset
from peft import AutoPeftModelForCausalLM, LoraConfig
from tqdm import tqdm
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    TrainingArguments,
)

from trl import SFTTrainer

from trl.trainer import ConstantLengthDataset

/usr/local/lib/python3.10/dist-packages/trl/trainer/ppo_config.py:141: UserWarning: The `optimize_cuda_cache` arguement will be deprecated soon, please use `optimize_device_cache` instead.
  warnings.warn(


- 허깅페이스 access token 넣고 로그인하기

In [3]:
from huggingface_hub import notebook_login

notebook_login()

- "nsmc" 데이터셋을 로드하기 위한 코드를 추가
	- nsmc 데이터셋을 메모리에 로드
	- 이를 my_dataset 변수에 할당

In [4]:
my_dataset=load_dataset("nsmc")#nsmc데이터셋 확인
my_dataset

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/150000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/50000 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'document', 'label'],
        num_rows: 150000
    })
    test: Dataset({
        features: ['id', 'document', 'label'],
        num_rows: 50000
    })
})

드라이브 마운트 후 파일 업로드
- dataset_infos.json

(수업에서 배운 것과 같이 huggingface에서 nsmc 데이터셋을 다운로드 받은 후 nlp 파일에 넣는다)

In [5]:
from google.colab import drive
drive.mount('/gdrive')

Mounted at /gdrive


In [ ]:
# 내가 업로드한 경로 기억 해둠

# /gdrive/MyDrive/nlp/dataset_infos.json

# 매개 변수 설정

- 사용할 데이터셋의 이름을 명시적으로 "nsmc"로 설정하기 위해
- ScriptArguments 클래스의 dataset_name을 None에서 "nsmc"로 변경

In [6]:
@dataclass
class ScriptArguments:
    cache_dir: Optional[str] = field(
        default=None, metadata={"help": "the cache dir"}
    )
    model_name: Optional[str] = field(
        default="meta-llama/Llama-2-7b-chat-hf", metadata={"help": "the model name"}
    )

    dataset_name: Optional[str] = field(
        default="nsmc",#dataset의 이름을 None에서 nsmc로 수정
        metadata={"help": "the dataset name"},
    )
    seq_length: Optional[int] = field(
        default=1024, metadata={"help": "the sequence length"}
    )
    num_workers: Optional[int] = field(
        default=8, metadata={"help": "the number of workers"}
    )
    training_args: TrainingArguments = field(
        default_factory=lambda: TrainingArguments(
            output_dir="./results",
            # max_steps=500,
            logging_steps=20,
            # save_steps=10,
            per_device_train_batch_size=1,
            per_device_eval_batch_size=1,
            gradient_accumulation_steps=2,
            gradient_checkpointing=False,
            group_by_length=False,
            learning_rate=1e-4,
            lr_scheduler_type="cosine",
            # warmup_steps=100,
            warmup_ratio=0.03,
            max_grad_norm=0.3,
            weight_decay=0.05,
            save_total_limit=20,
            save_strategy="epoch",
            num_train_epochs=1,
            optim="paged_adamw_32bit",
            fp16=True,
            remove_unused_columns=False,
            report_to="wandb",
        )
    )

    packing: Optional[bool] = field(
        default=True, metadata={"help": "whether to use packing for SFTTrainer"}
    )

    peft_config: LoraConfig = field(
        default_factory=lambda: LoraConfig(
            r=8,
            lora_alpha=16,
            lora_dropout=0.05,
            target_modules=["c_attn", "c_proj", "c_fc"],
            bias="none",
            task_type="CAUSAL_LM",
        )
    )

    merge_with_final_checkpoint: Optional[bool] = field(
        default=False, metadata={"help": "Do only merge with final checkpoint"}
    )

# 유틸리티

In [7]:
def chars_token_ratio(dataset, tokenizer, nb_examples=400): # helper 함수
    """
    Estimate the average number of characters per token in the dataset.
    """
    total_characters, total_tokens = 0, 0
    for _, example in tqdm(zip(range(nb_examples), iter(dataset)), total=nb_examples):
        text = prepare_sample_text(example)
        total_characters += len(text)
        if tokenizer.is_fast:
            total_tokens += len(tokenizer(text).tokens())
        else:
            total_tokens += len(tokenizer.tokenize(text))

    return total_characters / total_tokens


def print_trainable_parameters(model): # helper 함수
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

# 데이터 로딩

- 더 정확한 출력 결과를 위해 default_system_msg를 수정하였음
- 딕셔너리에 document와 label이 있는지 확인하는 코드를 추가하였음
- example이 문자열인 경우 처리하는 코드를 추가하였음

- 이 딕셔너리에서 document는 리뷰 텍스트(string)을, label은 감성 라벨(label)을 나타냄
- 따라서 라벨이 1이면 '긍정', 그렇지 않으면 '부정'을 출력하도록 수정하였음

In [8]:
def prepare_sample_text(example):
    """Prepare the text from a sample of the dataset."""

    prompt_template = """###System;{System}
    \n###User;{User}
    \n###Midm;{Midm}"""

    default_system_msg = ( # 더 정확한 출력 결과를 위해 default_system_msg를 수정하였음
       "너는 먼저 사용자가 작성한 리뷰의 긍정 또는 부정여부를 판단해야 한다. 이로부터 첫번째로 리뷰를 출력하고 두번째로 그에 대한 결과를 '긍정' 또는 '부정' 으로 출력해야한다."
    )

    # 딕셔너리에 document와 label이 있는지 확인하는 코드 (뒤에 에러 해결하며 코드 추가)
    if isinstance(example, dict):
        label = int(example["label"])
        text = (
            prompt_template.format(System=default_system_msg,
                                   User=example["document"],
                                   Midm="긍정" if label == 1 else "부정")
        )
    # example이 문자열인 경우 처리하는 코드
    elif isinstance(example, str):
        text = prompt_template.format(System=default_system_msg, User=example, Midm="Unknown")
    else:
        print(f"Unsupported example format: {type(example)}")
        raise ValueError("Unsupported example format")

    return text

base_model을 위한 def create_datasets
- NSMC의 train 스플릿 앞쪽 2,000개 이상의 샘플을 학습에 사용하는 조건 충족을 위해 코드 수정
    - train_data = dataset['train'].select(range(2000))
- 테스트는 test 스플릿 앞쪽 1,000개의 샘플만 측정하는 조건 충족을 위해 코드 수정
    - valid_data = dataset['test'].select(range(1000))

In [9]:
# base_model 실행할 때 사용하는 def create_datasets

def create_datasets(tokenizer, args):
    dataset = load_dataset(args.dataset_name, cache_dir=args.cache_dir)
    train_data = dataset['train'].select(range(2000)) # NSMC의 train 스플릿 앞쪽 2,000개 이상의 샘플을 학습에 사용
    valid_data = dataset['test'].select(range(1000)) # test 스플릿 앞쪽 1,000개의 샘플만 측정하는 조건 충족

    chars_per_token = chars_token_ratio(train_data, tokenizer)
    print(f"The character to token ratio of the dataset is: {chars_per_token:.2f}")

    train_dataset = ConstantLengthDataset(
        tokenizer,
        train_data,
        formatting_func=prepare_sample_text,
        infinite=True,
        seq_length=args.seq_length,
        chars_per_token=chars_per_token,
    )

    valid_dataset = ConstantLengthDataset( # 교수님 설명대로 base_model에서는 ConstantLengthDataset
        tokenizer,
        valid_data,
        formatting_func=prepare_sample_text,
        infinite=False,
        seq_length=args.seq_length,
        chars_per_token=chars_per_token,
    )
    return train_dataset, valid_dataset

trained_model을 위한 def create_datasets
- NSMC의 train 스플릿 앞쪽 2,000개 이상의 샘플을 학습에 사용하는 조건 충족을 위해 코드 수정
    - train_data = dataset['train'].select(range(2000))
- 테스트는 test 스플릿 앞쪽 1,000개의 샘플만 측정하는 조건 충족을 위해 코드 수정
    - valid_data = dataset['test'].select(range(1000))
- base_model로 미세튜닝 후 테스트 할 때에는 ConstantLengthDataset 대신 load_dataset을 이용
    - valid_dataset = load_dataset(
        script_args.dataset_name,
        cache_dir=script_args.cache_dir)["test"].select(range(1000))
    - 1000개를 골라서 테스트해야하므로 select(range(1000)) 코드를 추가하였음

In [9]:
# trained_model 실행할 때 사용하는 def create_datasets
# 교수님이 tip ppt #4. 최종 테스트 시 ConstantLengthDataset 금지

def create_datasets(tokenizer, args):
    dataset = load_dataset(args.dataset_name, cache_dir=args.cache_dir)
    train_data = dataset["train"].select(range(2000)) # NSMC의 train 스플릿 앞쪽 2,000개 이상의 샘플을 학습에 사용
    valid_data = dataset["test"].select(range(1000)) # test 스플릿 앞쪽 1,000개의 샘플만 측정하는 조건 충족

    chars_per_token = chars_token_ratio(train_data, tokenizer)
    print(f"The character to token ratio of the dataset is: {chars_per_token:.2f}")

    train_dataset = ConstantLengthDataset(
        tokenizer,
        train_data,
        formatting_func=prepare_sample_text,
        infinite=True,
        seq_length=args.seq_length,
        chars_per_token=chars_per_token,
    )
    valid_dataset = load_dataset(
        script_args.dataset_name,
        cache_dir=script_args.cache_dir)["test"].select(range(1000)) # range(1000)

    print(len(train_dataset), len(valid_dataset))
    return train_dataset, valid_dataset

# 미세 튜닝용 모델 로딩

- dataset_name을 'nsmc'로 지정해주는 코드 추가
    - dataset_name='nsmc'
- model_name을 KT-AI/midm-bitext-S-7B-inst-v1으로 수정
    - model_name='KT-AI/midm-bitext-S-7B-inst-v1'

In [10]:
script_args = ScriptArguments(
    num_workers=2,
    seq_length=384,
    dataset_name='nsmc',
    model_name='KT-AI/midm-bitext-S-7B-inst-v1',
    # model_name='jangmin/midm-7b-safetensors-only',
    )

- script_args.training_args.logging_step과 script_args.training_args.max_steps의 값을 적절히 수정
    - script_args.training_args.logging_steps = 100
        - 로깅 스텝을 100으로 설정하여 100 스텝마다 로깅 정보를 출력할 수 있도록 빈도를 결정함
    - script_args.training_args.max_steps = 2000
        - 최대 학습 스텝을 2000으로 설정하여, 2000 스텝 후 학습을 중단하도록 함
- 파일 경로를 수정
    - script_args.training_args.output_dir = '/gdrive/MyDrive/nlp/hw-midm-7B-nsmc'
        - 학습 결과를 저장할 위치를 결정
- 실행 이름을 'hw-midm-7B-nsmc'로 설정하여 로깅 및 모델 체크 포인트에 사용되도록 함
    - script_args.training_args.run_name = 'hw-midm-7B-nsmc'
- 최근 3개의 체크포인트만 유지하도록 설정하는 코드 추가
    - script_args.training_args.save_total_limit=3
- 지정된 스텝마다 체크포인트가 저장되도록 하는 코드 추가
    - script_args.training_args.save_strategy="steps"
- 300 스텝마다 체크포인트가 저장되도록 하는 코드 추가
    - script_args.training_args.save_steps=300

In [11]:
script_args.training_args.logging_steps = 100
script_args.training_args.max_steps = 2000
script_args.training_args.output_dir = '/gdrive/MyDrive/nlp/hw-midm-7B-nsmc'
script_args.training_args.run_name = 'hw-midm-7B-nsmc'
script_args.training_args.save_total_limit=3 # 최근 3개의 체크포인트만 유지하는 코드 추가
script_args.training_args.save_strategy="steps" # 지정된 스텝마다 체크포인트가 저장되도록 하는 코드 추가
script_args.training_args.save_steps=300 # 300스텝마다 체크 포인트가 저장되도록 하는 코드 추가

In [ ]:
print(script_args)

ScriptArguments(cache_dir=None, model_name='KT-AI/midm-bitext-S-7B-inst-v1', dataset_name='nsmc', seq_length=384, num_workers=2, training_args=TrainingArguments(
_n_gpu=1,
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_pin_memory=True,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=False,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_steps=None,
evaluation_strategy=no,
fp16=True,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
fsdp=[],
fsdp_config={'min_num_params': 0, 'xla': False, 'xla_fsdp_grad_ckpt': False},
fsdp_min_num_params=0,
fsdp_transformer_layer_cls_to_wrap=None,
full_determinism=False,
gradient_accumulation_steps

In [12]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

원본인 'KT-AI/midm-bitext-S-7B-inst-v1' 는 *.bin 형태로 모델을 제공한다.
- 코랩에서 CPU 메모리 부족 발생

해결책
- safetensors로 변환한 모델을 업로드 하고 이를 사용하기로 한다.

###⭐ base_model로 미세튜닝 완료 후, trained_model을 시행하기 ⭐

- base_model에 대해서 먼저 훈련 수행한 뒤,
- trained_model로 미세튜닝된 모델을 로딩한 뒤 테스트를 수행

base_model에 대한 훈련
- base_model = AutoModelForCausalLM.from_pretrained()
    - 에러 발생으로 token=True와 is_trainable=True 코드를 주석처리 하였음

In [13]:
# base_model에 대해 훈련
base_model = AutoModelForCausalLM.from_pretrained(
    script_args.model_name,
    quantization_config=bnb_config,
    device_map="auto",  # {"": Accelerator().local_process_index},
    #token=True, # 에러 발생으로 use auth token을 수정하였음
    #is_trainable=True,
    cache_dir=script_args.cache_dir,
    trust_remote_code=True,
)
base_model.config.use_cache = False

config.json:   0%|          | 0.00/1.14k [00:00<?, ?B/s]

configuration_midm.py:   0%|          | 0.00/831 [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co./KT-AI/midm-bitext-S-7B-inst-v1:
- configuration_midm.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


modeling_midm.py:   0%|          | 0.00/61.1k [00:00<?, ?B/s]

rotary_position_embedding.py:   0%|          | 0.00/4.06k [00:00<?, ?B/s]

...

model.safetensors.index.json:   0%|          | 0.00/25.4k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.97G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/6.22G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

trained_model 시행
- trained_model = AutoModelForCausalLM.from_pretrained()

In [13]:
#trained_model용
trained_model = AutoModelForCausalLM.from_pretrained(
    script_args.training_args.output_dir,
    quantization_config=bnb_config,
    device_map="auto",  # {"": Accelerator().local_process_index},
    trust_remote_code=True,
    token=True,  # use oath token 대신 사용
    cache_dir=script_args.cache_dir,
)
trained_model.config.use_cache = False

config.json:   0%|          | 0.00/1.14k [00:00<?, ?B/s]

configuration_midm.py:   0%|          | 0.00/831 [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co./KT-AI/midm-bitext-S-7B-inst-v1:
- configuration_midm.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


modeling_midm.py:   0%|          | 0.00/61.1k [00:00<?, ?B/s]

rotary_position_embedding.py:   0%|          | 0.00/4.06k [00:00<?, ?B/s]

...

model-00001-of-00002.safetensors:   0%|          | 0.00/9.97G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/6.22G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/utils/hub.py:374: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

In [ ]:
base_model

MidmLMHeadModel(
  (transformer): MidmModel(
    (wte): Embedding(72192, 4096)
    (rotary_pos_emb): RotaryEmbedding()
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-31): 32 x MidmBlock(
        (ln_1): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attn): MidmAttention(
          (c_attn): Linear4bit(in_features=4096, out_features=12288, bias=False)
          (c_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
        )
        (ln_2): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (mlp): MidmMLP(
          (c_fc): Linear4bit(in_features=4096, out_features=21760, bias=False)
          (c_proj): Linear4bit(in_features=10880, out_features=4096, bias=False)
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
  )
 

In [14]:
peft_config = script_args.peft_config # peft_config 변수에 script_args.peft_config의 값을 할당하는 코드

In [ ]:
peft_config

- ⭐ base_model을 실행할 때 해당 코드 실행 ⭐ (trained_model 시행 시 x)
    - base_model.config.pad_token_id = tokenizer.pad_token_id
    - base_model.config.bos_token_id = tokenizer.bos_token_id

In [15]:
tokenizer = AutoTokenizer.from_pretrained(
    script_args.model_name,
    trust_remote_code=True,
    cache_dir=script_args.cache_dir,
)

if getattr(tokenizer, "pad_token", None) is None:
    tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"  # Fix weird overflow issue with fp16 training

tokenizer.add_special_tokens(dict(bos_token='<s>'))

base_model.config.pad_token_id = tokenizer.pad_token_id
base_model.config.bos_token_id = tokenizer.bos_token_id

tokenizer_config.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

midm_bitext_tokenization.py:   0%|          | 0.00/12.8k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co./KT-AI/midm-bitext-S-7B-inst-v1:
- midm_bitext_tokenization.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


midm_bitext_tokenizer.model:   0%|          | 0.00/1.46M [00:00<?, ?B/s]

- ⭐ trained_model을 실행할 때 해당 코드 실행 ⭐ (base_model 시행 시 x)
    - trained_model.config.pad_token_id = tokenizer.pad_token_id
    - trained_model.config.bos_token_id = tokenizer.bos_token_id

In [15]:
tokenizer = AutoTokenizer.from_pretrained(
    script_args.model_name,
    trust_remote_code=True,
    cache_dir=script_args.cache_dir,
)

if getattr(tokenizer, "pad_token", None) is None:
    tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"  # Fix weird overflow issue with fp16 training

tokenizer.add_special_tokens(dict(bos_token='<s>'))

trained_model.config.pad_token_id = tokenizer.pad_token_id
trained_model.config.bos_token_id = tokenizer.bos_token_id

tokenizer_config.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

midm_bitext_tokenization.py:   0%|          | 0.00/12.8k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co./KT-AI/midm-bitext-S-7B-inst-v1:
- midm_bitext_tokenization.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


midm_bitext_tokenizer.model:   0%|          | 0.00/1.46M [00:00<?, ?B/s]

In [16]:
training_args = script_args.training_args # training_args 변수에 script_args.training_args의 값을 할당하는 코드

In [17]:
train_dataset, valid_dataset = create_datasets(tokenizer, script_args) # create_datasets 함수를 호출하여 학습 데이터셋 (train_dataset)과 검증 데이터셋 (valid_dataset)을 생성 -> 100%

100%|██████████| 400/400 [00:00<00:00, 4132.93it/s]
/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:548: UserWarning: The passed formatting_func has more than one argument. Usually that function should have a single argument `example` which corresponds to the dictionary returned by each element of the dataset. Make sure you know what you are doing.
  warnings.warn(


The character to token ratio of the dataset is: 1.51
2000 1000


In [ ]:
print(len(train_dataset),len(valid_dataset))

2000 1000


- ⭐ base_model을 실행할 때 해당 코드 실행 ⭐ (trained_model 시행 시 x)

In [18]:
# base_model용

trainer = SFTTrainer(
    model=base_model,
    train_dataset=train_dataset,
    eval_dataset=None,
    peft_config=peft_config,
    #peft_config=None, # 교수님께서는 None으로 수정하라 하셨지만 에러 발생으로 본래 peft_config로 실행
    packing=script_args.packing,
    max_seq_length=script_args.seq_length,
    tokenizer=tokenizer,
    args=training_args,
)

/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:267: UserWarning: You passed `packing=True` to the SFTTrainer, and you are training your model with `max_steps` strategy. The dataset will be iterated until the `max_steps` are reached.
  warnings.warn(


In [ ]:
base_model

MidmLMHeadModel(
  (transformer): MidmModel(
    (wte): Embedding(72192, 4096)
    (rotary_pos_emb): RotaryEmbedding()
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-31): 32 x MidmBlock(
        (ln_1): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attn): MidmAttention(
          (c_attn): Linear4bit(
            (lora_dropout): ModuleDict(
              (default): Dropout(p=0.05, inplace=False)
            )
            (lora_A): ModuleDict(
              (default): Linear(in_features=4096, out_features=8, bias=False)
            )
            (lora_B): ModuleDict(
              (default): Linear(in_features=8, out_features=12288, bias=False)
            )
            (lora_embedding_A): ParameterDict()
            (lora_embedding_B): ParameterDict()
            (base_layer): Linear4bit(in_features=4096, out_features=12288, bias=False)
          )
          (c_proj): Linear4bit(
            (lora_dropout): ModuleDict(
              (default):

In [ ]:
trainer.model

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): MidmLMHeadModel(
      (transformer): MidmModel(
        (wte): Embedding(72192, 4096)
        (rotary_pos_emb): RotaryEmbedding()
        (drop): Dropout(p=0.0, inplace=False)
        (h): ModuleList(
          (0-31): 32 x MidmBlock(
            (ln_1): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
            (attn): MidmAttention(
              (c_attn): Linear4bit(
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=8, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=8, out_features=12288, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (base_layer): Linear4bit(in_features=

In [ ]:
print_trainable_parameters(base_model)

trainable params: 16744448 || all params: 3821510656 || trainable%: 0.4381630592527648


In [ ]:
base_model.get_memory_footprint()

7795015808

In [ ]:
trainer.model.print_trainable_parameters()

trainable params: 16,744,448 || all params: 7,034,347,520 || trainable%: 0.23803839591934178


midm 모델을 'nsmc'에 적용시 특징

- 구글 코랩 T-4 GPU: 1000스텝 (1:33:426 예상)
- 14.7 G / 15.0 G 사용

- wandb.ai의 API key를 입력하고 로그인
- 2000 모두 될 때까지 학습하며 checkpoint가 잘 담기는지 확인

In [19]:
trainer.train()

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:570: UserWarning: The dataset reached end and the iterator is reset to the start.
  warnings.warn("The dataset reached end and the iterator is reset to the start.")


/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:570: UserWarning: The dataset reached end and the iterator is reset to the start.
  warnings.warn("The dataset reached end and the iterator is reset to the start.")
/usr/local/lib/python3.10/dist-packages/torch/utils/data/dataloader.py:642: UserWarning: Length of IterableDataset <trl.trainer.utils.ConstantLengthDataset object at 0x7bf4e0a0c2e0> was reported to be 2000 (when accessing len(dataloader)), but 2001 samples have been fetched. 
  warnings.warn(warn_msg)
/usr/local/lib/python3.10/dist-packages/torch/utils/data/dataloader.py:642: UserWarning: Length of IterableDataset <trl.trainer.utils.ConstantLengthDataset object at 0x7bf4e0a0c2e0> was reported to be 2000 (when accessing len(dataloader)), but 2002 samples have been fetched. 
  warnings.warn(warn_msg)
/usr/local/lib/python3.10/dist-packages/torch/utils/data/dataloader.py:642: UserWarning: Length of IterableDataset <trl.trainer.utils.ConstantLengthDataset object at 0x

TrainOutput(global_step=2000, training_loss=0.4290015735626221, metrics={'train_runtime': 6133.9487, 'train_samples_per_second': 0.652, 'train_steps_per_second': 0.326, 'total_flos': 6.2103389995008e+16, 'train_loss': 0.4290015735626221, 'epoch': 2.0})

In [18]:
script_args.training_args.output_dir # trainer.train() 이후 학습 결과를 저장할 디렉토리 경로를 나타내는 코드

'/gdrive/MyDrive/nlp/hw-midm-7B-nsmc'

In [19]:
trainer.save_model(script_args.training_args.output_dir) # trainer.save_model 함수를 호출하여 모델을 저장

NameError: ignored

# 추론 테스트

In [20]:
from transformers import pipeline, TextStreamer

- prepare_sample_text()에서 생성한 프롬프트와 테스트 때의 프롬프트가 같아야 함
    - default_system_msg = (
    "너는 먼저 사용자가 작성한 리뷰의 긍정 또는 부정여부를 판단해야 한다. 이로부터 첫번째로 리뷰를 출력하고 두번째로 그에 대한 결과를 '긍정' 또는 '부정' 으로 출력해야한다."
)

In [21]:
instruction_prompt_template = """###System;다음은 네이버 영화의 리뷰문장이다.이를 분석하여 리뷰문장이 긍정인지 부정인지를 분류하고자 한다. 리뷰와 긍정,부정 여부를 출력하는 분석결과를 완성해주기를 바란다.

### 리뷰: {0} ### 분석 결과:
"""

prompt_template = """###System;{System}
\n###User;{User}
\n###Midm;"""

default_system_msg = (
    "너는 먼저 사용자가 작성한 리뷰의 긍정 또는 부정여부를 판단해야 한다. 이로부터 첫번째로 리뷰를 출력하고 두번째로 그에 대한 결과를 '긍정' 또는 '부정' 으로 출력해야한다."
)

In [22]:
evaluation_queries = [
    "아 더빙.. 진짜 짜증나네요 목소리",
    "흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나",
    "너무재밓었다그래서보는것을추천한다",
    "교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정",
    "사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 던스트가 너무나도 이뻐보였다",
    "액션이 없는데도 재미 있는 몇안되는 영화",
    "왜케 평점이 낮은건데? 꽤 볼만한데.. 헐리우드식 화려함에만 너무 길들여져 있나?",
    "걍인피니트가짱이다.진짜짱이다♥",
    "볼때마다 눈물나서 죽겠다90년대의 향수자극!!허진호는 감성절제멜로의 달인이다~"
]

In [23]:
def wrapper_generate(model, input_prompt, do_stream=False):
    data = tokenizer(input_prompt, return_tensors="pt")
    streamer = TextStreamer(tokenizer, skip_prompt=True, skip_special_tokens=True)
    input_ids = data.input_ids[..., :-1]
    with torch.no_grad():
        pred = model.generate(
            input_ids=input_ids.cuda(),
            streamer=streamer if do_stream else None,
            use_cache=True,
            max_new_tokens=float('inf'),
            do_sample=False
        )
    decoded_text = tokenizer.batch_decode(pred, skip_special_tokens=True)
    decoded_text = decoded_text[0].replace("<[!newline]>", "\n")
    return (decoded_text[len(input_prompt):])

In [ ]:
eval_dic = {i:wrapper_generate(model=trained_model, input_prompt=prompt_template.format(System=default_system_msg, User=evaluation_queries[i]))for i, query in enumerate(evaluation_queries)}

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1473: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use and modify the model generation configuration (see https://huggingface.co./docs/transformers/generation_strategies#default-text-generation-configuration )
  warnings.warn(


In [ ]:
print(eval_dic[0])

 긍정


# 미세튜닝된 모델 로딩 후 테스트

In [ ]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

In [ ]:
trained_model = AutoPeftModelForCausalLM.from_pretrained(
    script_args.training_args.output_dir,
    quantization_config=bnb_config,
    device_map="auto",
    cache_dir=script_args.cache_dir,
    trust_remote_code=True,
)

ValueError: ignored

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(
    script_args.model_name,
    trust_remote_code=True,
    cache_dir=script_args.cache_dir,
)

if getattr(tokenizer, "pad_token", None) is None:
    tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"  # Fix weird overflow issue with fp16 training

tokenizer.add_special_tokens(dict(bos_token='<s>'))

trained_model.config.pad_token_id = tokenizer.pad_token_id
trained_model.config.bos_token_id = tokenizer.bos_token_id

- valid_dataset 데이터셋에서 처음 1000개의 항목만 선택해 새로운 valid_dataset을 생성하는 코드 추가
    - valid_dataset=valid_dataset.select(range(1000))

In [ ]:
valid_dataset=valid_dataset.select(range(1000))

- 앞서 load_dataset 부분으로 수정하였으므로 입력 프롬프트를 설정하는 코드도 수정
    - User을 valid_dataset[i]로 수정하고 valid_dataset을 반환할 수 있도록 함
        - eval_dic = {i:wrapper_generate(model=trained_model, do_stream=True, input_prompt=prompt_template.format(System=default_system_msg, User=valid_dataset[i]))for i, query in enumerate(valid_dataset)}

In [24]:
eval_dic = {i:wrapper_generate(model=trained_model, do_stream=True, input_prompt=prompt_template.format(System=default_system_msg, User=valid_dataset[i]))for i, query in enumerate(valid_dataset)}

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1473: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use and modify the model generation configuration (see https://huggingface.co./docs/transformers/generation_strategies#default-text-generation-configuration )
  warnings.warn(


긍정
긍정
부정
부정
부정
긍정
부정
부정
부정
긍정
긍정
긍정
긍정
긍정
부정
부정
긍정
부정
긍정
부정
긍정
부정
긍정
긍정
부정
긍정
긍정
긍정
부정
긍정
긍정
긍정
부정
긍정
부정
부정
부정
긍정
부정
긍정
부정
부정
부정
긍정
부정
긍정
긍정
부정
긍정
긍정
부정
부정
부정
긍정
긍정
긍정
부정
긍정
긍정
긍정
부정
부정
부정
부정
긍정
부정
긍정
긍정
긍정
긍정
부정
부정
부정
부정
부정
긍정
긍정
긍정
긍정
부정
부정
긍정
긍정
긍정
부정
긍정
긍정
부정
긍정
부정
부정
긍정
부정
부정
부정
부정
긍정
긍정
부정
긍정
부정
부정
긍정
부정
긍정
부정
긍정
부정
긍정
긍정
부정
긍정
긍정
긍정
긍정
부정
긍정
긍정
긍정
긍정
긍정
부정
긍정
긍정
부정
긍정
부정
긍정
부정
긍정
부정
긍정
부정
긍정
긍정
부정
긍정
긍정
긍정
긍정
부정
부정
긍정
긍정
부정
긍정
부정
부정
부정
부정
긍정
부정
긍정
긍정
긍정
긍정
긍정
부정
긍정
부정
긍정
긍정
긍정
긍정
긍정
긍정
긍정
긍정
긍정
부정
부정
부정
부정
긍정
긍정
부정
긍정
부정
부정
긍정
긍정
긍정
부정
부정
긍정
긍정
부정
부정
부정
긍정
긍정
부정
긍정
긍정
긍정
부정
긍정
긍정
부정
부정
부정
긍정
긍정
긍정
긍정
긍정
긍정
부정
부정
긍정
부정
긍정
부정
긍정
부정
부정
부정
긍정
긍정
부정
긍정
긍정
부정
부정
부정
긍정
긍정
부정
긍정
긍정
부정
부정
긍정
긍정
긍정
긍정
부정
긍정
부정
부정
부정
부정
긍정
긍정
부정
긍정
긍정
긍정
긍정
부정
부정
부정
부정
부정
부정
긍정
긍정
긍정
부정
긍정
부정
긍정
긍정
긍정
긍정
긍정
긍정
부정
긍정
긍정
긍정
부정
부정
긍정
긍정
긍정
부정
긍정
부정
긍정
긍정
긍정
긍정
부정
부정
부정
긍정
긍정
부정
긍정
긍정
긍정
긍정
부정
긍정
부정
긍정
부정
긍정
긍정
긍정
긍정
긍정
부정
부정
긍정
부정
긍정
긍정
긍정
부정
긍정
긍정
부정
부정
부정
부정
부정
부정
긍정
부정
부정
긍정
긍정
부정
긍정
부정
긍정
부정
부정
긍정
긍정
부정
부

- accuracy 정확도를 측정하는 코드를 추가하였음

In [25]:
correct_predictions = 0
total_examples = len(valid_dataset)

for i, query in enumerate(valid_dataset):
    actual_label = int(query["label"])
    predicted_label = 1 if eval_dic[i] == "긍정" else 0

    if actual_label == predicted_label:
        correct_predictions += 1

accuracy = correct_predictions / total_examples
print(f"Accuracy: {accuracy * 100:.2f}%")


Accuracy: 90.60%


In [ ]:
print(eval_dic[0])

 긍정


- 정확도를 표로 출력하기 위한 코드

In [26]:
import pandas as pd

# 데이터를 저장할 빈 딕셔너리를 생성
data = {'TP': [0, 0], 'TN': [0, 0]}
correct_predictions = 0

for i, query in enumerate(valid_dataset):
    actual_label = int(query["label"])
    predicted_label = 1 if eval_dic[i] == "긍정" else 0  # Assuming "긍정" is positive, "부정" is negative

    # 예측이 긍정인 경우
    if predicted_label == 1:
        # 실제 레이블이 긍정인 경우
        if actual_label == 1:
            data['TP'][0] += 1  # PP
            correct_predictions += 1
        # 실제 레이블이 부정인 경우
        else:
            data['TP'][1] += 1  # PN
    # 예측이 부정인 경우
    else:
        # 실제 레이블이 긍정인 경우
        if actual_label == 1:
            data['TN'][0] += 1  # PP
        # 실제 레이블이 부정인 경우
        else:
            data['TN'][1] += 1  # PN
            correct_predictions += 1

# 데이터를 DataFrame으로 변환
df = pd.DataFrame(data, index=['PP', 'PN'])

# 전체 정확도를 계산
accuracy = correct_predictions / len(valid_dataset)

# 정확도를 DataFrame에 추가
df.loc['Accuracy'] = ["-", accuracy]

# DataFrame을 출력
print(df)

           TP       TN
PP        452   56.000
PN         38  454.000
Accuracy    -    0.906
